In [6]:
import numpy as np
import scipy
import scipy.stats
import pandas as pd
import astropy.units as u
import sunpy.map
import sunpy.visualization.colormaps as cm
import sunpy.data.sample
import reproject
import cv2
from sklearn.cluster import KMeans
from PIL import Image
from copy import copy
import datetime

import cv2

import matplotlib.pyplot as plt
import matplotlib.colors as colors
import seaborn as sns
import seaborn_image as isns
sns.set_style("darkgrid")

import os

import glob
import random

import utils
import tarfile

%matplotlib inline

In [7]:
hmiM_dir = "data/hmi_magnetogram"
hmiM_files = os.listdir(hmiM_dir)
hmiM_date_format = "%Y-%m-%dT%H-%M-%S.fits"
hmiM_dates = [datetime.datetime.strptime(i, hmiM_date_format) for i in hmiM_files]

aia193_dir = "data/aia_193A/"
aia193_files = os.listdir(aia193_dir)
aia193_date_format = "%Y-%m-%dT%H-%M-%S.fits"
aia193_dates = [datetime.datetime.strptime(i, aia193_date_format) for i in aia193_files]

aia211_dir = "data/aia_211A/"
aia211_files = os.listdir(aia211_dir)
aia211_date_format = "%Y-%m-%dT%H-%M-%S.fits"
aia211_dates = [datetime.datetime.strptime(i, aia211_date_format) for i in aia211_files]

## We take as a reference AIA193A and project the rest to it

In [8]:
corrupt_idx = [8197, 10021, 20118, 21086, 22198, 23608]
bad_idx = [998, 2790, 2843, 3715, 4203, 4429]

if not os.path.exists("data/composite_data_polar"):
    os.makedirs("data/composite_data_polar")

for aia193_idx, aia193_ref_file in enumerate(aia193_files):
    new_file_name = aia193_ref_file.replace('.fits', '.npy')

    if os.path.exists(f"data/composite_data_polar/{new_file_name}"):
        print(f"file \"data/composite_data_polar/{new_file_name}\" already exists")
        continue
    
    hmiM_date_dist = [abs(aia193_dates[aia193_idx] - ref_date) for ref_date in hmiM_dates]
    aia211_date_dist = [abs(aia193_dates[aia193_idx] - ref_date) for ref_date in aia211_dates]

    if max(min(hmiM_date_dist), min(aia211_date_dist)) < datetime.timedelta(hours=2) and aia193_idx not in corrupt_idx:
        print(aia193_idx)
        hmiM_idx = hmiM_date_dist.index(min(hmiM_date_dist))
        aia211_idx = aia211_date_dist.index(min(aia211_date_dist))


        aia193_map = sunpy.map.Map("data/aia_193A/" + aia193_ref_file)
        aia211_map = sunpy.map.Map("data/aia_211A/" + aia211_files[aia211_idx])
        hmiM_map = sunpy.map.Map("data/hmi_magnetogram/" + hmiM_files[hmiM_idx])


        new_hmiM_map = hmiM_map.reproject_to(aia193_map.wcs)
        new_aia211_map = aia211_map.reproject_to(aia193_map.wcs)

        polar_aia193 = utils.map_to_polar(aia193_map)
        polar_aia211 = utils.map_to_polar(new_aia211_map)
        polar_hmiM = utils.map_to_polar(new_hmiM_map)

        composite_data = np.stack([polar_aia193, polar_aia211, polar_hmiM], axis=2)
        
        np.save(f"data/composite_data_polar/{new_file_name}", composite_data)
        print(f"Saved tensor of size {composite_data.shape} to \"data/composite_data_polar/{new_file_name}\"")

file "data/composite_data_polar/2019-11-28T04-53-27.npy" already exists
file "data/composite_data_polar/2019-10-31T05-22-26.npy" already exists
file "data/composite_data_polar/2016-02-01T03-34-35.npy" already exists
file "data/composite_data_polar/2018-11-18T08-45-01.npy" already exists
file "data/composite_data_polar/2015-06-21T05-47-23.npy" already exists
file "data/composite_data_polar/2015-11-28T04-43-04.npy" already exists
file "data/composite_data_polar/2016-04-18T03-41-02.npy" already exists
file "data/composite_data_polar/2019-11-15T11-52-18.npy" already exists
file "data/composite_data_polar/2012-12-06T22-11-00.npy" already exists
file "data/composite_data_polar/2017-05-11T04-41-28.npy" already exists
file "data/composite_data_polar/2013-10-06T05-14-47.npy" already exists
file "data/composite_data_polar/2019-04-01T09-32-08.npy" already exists
file "data/composite_data_polar/2015-02-08T09-15-00.npy" already exists
file "data/composite_data_polar/2018-08-13T06-41-34.npy" already

In [9]:
corrupt_idx = [8197, 10021, 20118, 21086, 22198, 23608]
bad_idx = [998, 2790, 2843, 3715, 4203, 4429]

if not os.path.exists("data/composite_data"):
    os.makedirs("data/composite_data")

for aia193_idx, aia193_ref_file in enumerate(aia193_files):
    new_file_name = aia193_ref_file.replace('.fits', '.npy')

    if os.path.exists(f"data/composite_data/{new_file_name}"):
        print(f"file \"data/composite_data/{new_file_name}\" already exists")
        continue
    
    hmiM_date_dist = [abs(aia193_dates[aia193_idx] - ref_date) for ref_date in hmiM_dates]
    aia211_date_dist = [abs(aia193_dates[aia193_idx] - ref_date) for ref_date in aia211_dates]

    if max(min(hmiM_date_dist), min(aia211_date_dist)) < datetime.timedelta(hours=2) and aia193_idx not in corrupt_idx:
        print(aia193_idx)
        hmiM_idx = hmiM_date_dist.index(min(hmiM_date_dist))
        aia211_idx = aia211_date_dist.index(min(aia211_date_dist))


        aia193_map = sunpy.map.Map("data/aia_193A/" + aia193_ref_file)
        aia211_map = sunpy.map.Map("data/aia_211A/" + aia211_files[aia211_idx])
        hmiM_map = sunpy.map.Map("data/hmi_magnetogram/" + hmiM_files[hmiM_idx])

        new_hmiM_map = hmiM_map.reproject_to(aia193_map.wcs)
        new_aia211_map = aia211_map.reproject_to(aia193_map.wcs)
        
        new_hmiM_data = new_hmiM_map.data
        new_aia211_data = new_aia211_map.data
        new_aia193_data = aia193_map.data
        new_aia193_data[np.isnan(new_aia211_data)] = float('NaN')

        composite_data = np.stack([new_aia193_data, new_aia211_data, new_hmiM_data], axis=2)
        
        np.save(f"data/composite_data/{new_file_name}", composite_data)
        print(f"Saved tensor of size {composite_data.shape} to \"data/composite_data/{new_file_name}\"")

file "data/composite_data/2019-11-28T04-53-27.npy" already exists
file "data/composite_data/2019-10-31T05-22-26.npy" already exists
file "data/composite_data/2016-02-01T03-34-35.npy" already exists
file "data/composite_data/2018-11-18T08-45-01.npy" already exists
file "data/composite_data/2015-06-21T05-47-23.npy" already exists
file "data/composite_data/2015-11-28T04-43-04.npy" already exists
file "data/composite_data/2016-04-18T03-41-02.npy" already exists
file "data/composite_data/2019-11-15T11-52-18.npy" already exists
file "data/composite_data/2012-12-06T22-11-00.npy" already exists
file "data/composite_data/2017-05-11T04-41-28.npy" already exists
file "data/composite_data/2013-10-06T05-14-47.npy" already exists
file "data/composite_data/2019-04-01T09-32-08.npy" already exists
file "data/composite_data/2015-02-08T09-15-00.npy" already exists
file "data/composite_data/2018-08-13T06-41-34.npy" already exists
file "data/composite_data/2017-06-29T04-48-44.npy" already exists
file "data